# MultimodalsTrap

In [7]:
%load_ext autoreload
%autoreload 2

import sys; sys.path.append("../../")

from copy import deepcopy

import pandas as pd
from captum.attr import (DeepLift, DeepLiftShap, FeatureAblation,
                         FeaturePermutation, GradientShap, GuidedBackprop,
                         InputXGradient, IntegratedGradients, NoiseTunnel,
                         Saliency, ShapleyValueSampling)
from evobench import continuous, discrete, CompoundBenchmark
import plotly.io as pio
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks.early_stopping import EarlyStopping
from pytorch_lightning.utilities.seed import seed_everything
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import MinMaxScaler, StandardScaler

from hell import Surrogate, SurrogateData, plot, util
from hell.linkage import EmpiricalLinkage

seed_everything(42)
pio.renderers.default = "notebook"

Global seed set to 42
The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [9]:
benchmark = CompoundBenchmark(
    benchmarks=[
        discrete.Bimodal(blocks=[10] * 5),
        continuous.Trap(blocks=[10] * 5)
    ],
    verbose=1
)

x_preprocessing = Pipeline([
    ("standard-scaler", StandardScaler())
])

y_preprocessing = Pipeline([
    ("min-max-scaler", MinMaxScaler())
])

data = SurrogateData(
    benchmark,
    x_preprocessing, y_preprocessing,
    n_samples=2e5, splits=(0.6, 0.2, 0.2),
    batch_size=1000,
)

In [11]:
# ? sanity check

from xgboost import XGBRegressor
from sklearn.metrics import r2_score

xgb_model = XGBRegressor(n_estimators=200, nthread=8)
xgb_model.fit(data.x_train, data.y_train)
y_pred = xgb_model.predict(data.x_test)
r2_score(data.y_test, y_pred)


Initializing poptulation: 120000 samples
  2%|▏         | 2109/120000 [00:00<00:05, 20881.77it/s]
Evaluating population of 120000 solutions

  0%|          | 0/40000 [00:00<?, ?it/s]
Initializing poptulation: 40000 samples

Evaluating population of 40000 solutions

100%|██████████| 40000/40000 [00:01<00:00, 20986.37it/s]


0.7159870772580653

In [13]:
surrogate = Surrogate(
    benchmark.genome_size,
    x_preprocessing, y_preprocessing,
    n_layers=1, learning_rate=2e-4, weight_decay=1e-8
)

early_stop_callback = EarlyStopping(
   monitor="val/r2",
   min_delta=0.000,
   patience=5,
   verbose=False,
   mode="max"
)

trainer = Trainer(
    max_epochs=100,
    gpus=1,
    progress_bar_refresh_rate=50,
    callbacks=[early_stop_callback]
)

GPU available: True, used: True
TPU available: False, using: 0 TPU cores


In [15]:
trainer.fit(surrogate, data.data_module)
surrogate.eval()


Initializing poptulation: 40000 samples

Evaluating population of 40000 solutions
100%|██████████| 40000/40000 [00:01<00:00, 20586.40it/s]
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name     | Type       | Params
----------------------------------------
0 | linears  | ModuleList | 6.3 K 
1 | dropouts | ModuleList | 0     
2 | linear_n | Linear     | 26    
3 | sigmoid  | Sigmoid    | 0     
----------------------------------------
6.4 K     Trainable params
0         Non-trainable params
6.4 K     Total params
0.025     Total estimated model params size (MB)
                                                              c:\Code\academia\evo\hell-xai\env\lib\site-packages\pytorch_lightning\utilities\distributed.py:69: UserWarning:

The dataloader, val dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 16 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.

Glo

Surrogate(
  (linears): ModuleList(
    (0): Linear(in_features=100, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=25, bias=True)
  )
  (dropouts): ModuleList(
    (0): Dropout(p=0.2, inplace=False)
    (1): Dropout(p=0.2, inplace=False)
  )
  (linear_n): Linear(in_features=25, out_features=1, bias=True)
  (sigmoid): Sigmoid()
)

In [19]:
xai_results = util.test_xais(
    benchmark,
    data.x_preprocessing,
    decomposers=[
        EmpiricalLinkage(benchmark, DeepLift(surrogate), data.x_preprocessing),
        EmpiricalLinkage(benchmark, FeatureAblation(surrogate), data.x_preprocessing),
        EmpiricalLinkage(benchmark, GradientShap(surrogate), data.x_preprocessing),
        EmpiricalLinkage(benchmark, GuidedBackprop(surrogate), data.x_preprocessing),
        EmpiricalLinkage(benchmark, InputXGradient(surrogate), data.x_preprocessing),
        EmpiricalLinkage(benchmark, IntegratedGradients(surrogate), data.x_preprocessing),
        EmpiricalLinkage(benchmark, NoiseTunnel(IntegratedGradients(surrogate)), data.x_preprocessing),
        EmpiricalLinkage(benchmark, Saliency(surrogate), data.x_preprocessing),
    ],
    n_samples=100,
)

\gradient.py:55: UserWarning:

Input Tensor 0 did not already require gradients, required_grads has been set automatically.

c:\Code\academia\evo\hell-xai\env\lib\site-packages\captum\_utils\gradient.py:55: UserWarning:

Input Tensor 0 did not already require gradients, required_grads has been set automatically.

c:\Code\academia\evo\hell-xai\env\lib\site-packages\captum\_utils\gradient.py:55: UserWarning:

Input Tensor 0 did not already require gradients, required_grads has been set automatically.

c:\Code\academia\evo\hell-xai\env\lib\site-packages\captum\_utils\gradient.py:55: UserWarning:

Input Tensor 0 did not already require gradients, required_grads has been set automatically.

Testing XAIs:  88%|████████▊ | 7/8 [06:55<00:49, 49.76s/it]c:\Code\academia\evo\hell-xai\env\lib\site-packages\captum\_utils\gradient.py:55: UserWarning:

Input Tensor 0 did not already require gradients, required_grads has been set automatically.

c:\Code\academia\evo\hell-xai\env\lib\site-packages\capt

In [20]:
results = xai_results

In [21]:
plot.hit_ratio(results)

In [22]:
plot.ranking_metric(
    results,
    metric="mean_reciprocal_rank",
    title="Mean Reciprocal Ranking"
)

In [23]:
plot.ranking_metric(
    results,
    metric="mean_average_precision",
    title="Mean Average Precision"
)

In [24]:
plot.ranking_metric(
    results,
    metric="ndcg$1",
    title="NDCG$1"
)

In [25]:
results_mean = results.groupby(by="method").mean()

In [26]:
results_mean.T.to_csv("multimodals.csv")